In [1]:
import pandas as pd
import numpy as np
import math
import os # needed for addressing files by path when reading and writing
from scipy.io import arff #needed to read headers
import matplotlib.pyplot as plt
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
from sklearn import tree
#from sklearn.tree import DecisionTreeClassifierMLClient
from sklearn.ensemble import RandomForestClassifier

from sklearn.preprocessing import StandardScaler
import torch
from torch.utils.data import DataLoader, TensorDataset


/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [10]:
import sys

In [2]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f'Using device: {device}')

Using device: cpu


In [3]:
from azureml.core import Workspace, Experiment, Run
ws = Workspace.from_config()

# Create an experiment
experiment_name = 'malgenome'
experiment = Experiment(ws, experiment_name)

# Start a run
run = experiment.start_logging()


pip install azure-ai-ml
pip install azureml-fsspec
pip install fsspec

In [2]:

import pandas as pd
from azure.ai.ml import MLClient
from azure.identity import DefaultAzureCredential

ml_client = MLClient.from_config(credential=DefaultAzureCredential())
data_asset = ml_client.data.get("MALGENOME_1", version="1")

df = pd.read_csv(data_asset.path)
df

Found the config file in: /config.json


transact  bindService  onServiceConnected  ServiceConnection  \
0            0            0                   0                  0   
1            0            0                   0                  0   
2            0            0                   0                  0   
3            0            0                   0                  0   
4            1            1                   1                  1   
...        ...          ...                 ...                ...   
3794         0            1                   1                  1   
3795         1            1                   1                  1   
3796         0            0                   0                  0   
3797         1            1                   1                  1   
3798         0            0                   0                  0   

      android.os.Binder  READ_SMS  attachInterface  WRITE_SMS  \
0                     0         0                0          0   
1                     0         1                0          0   
2                     0         0                0          0   
3                     0         1                0          1   
4                     1         1                1          1   
...                 ...       ...              ...        ...   
3794                  0         0                0          0   
3795                  1         0                1          0   
3796                  0         0                0          0   
3797                  1         0                1          0   
3798                  0         0                0          0   

      TelephonyManager.getSubscriberId  Ljava.lang.Class.getCanonicalName  \
0                                    0                                  0   
1                                    1                                  0   
2                                    0                                  0   
3                                    1                                  0   
4                                    1                                  1   
...                                ...                                ...   
3794                                 0                                  1   
3795                                 0                                  1   
3796                                 0                                  0   
3797                                 0                                  1   
3798                                 0                                  0   

      ...  Ljava.lang.Object.getClass  SET_ORIENTATION  DEVICE_POWER  \
0     ...                           1                0             0   
1     ...                           1                0             0   
2     ...                           0                0             0   
3     ...                           1                0             0   
4     ...                           1                0             1   
...   ...                         ...              ...           ...   
3794  ...                           1                0             0   
3795  ...                           1                0             0   
3796  ...                           1                0             0   
3797  ...                           1                0             0   
3798  ...                           0                0             0   

      EXPAND_STATUS_BAR  GET_TASKS  GLOBAL_SEARCH  GET_PACKAGE_SIZE  \
0                     0          0              0                 0   
1                     0          0              0                 0   
2                     0          0              0                 0   
3                     0          0              0                 0   
4                     0          0              0                 0   
...                 ...        ...            ...               ...   
3794                  0          0              0                 0   
3795                  0   

KeyError: 'label'

In [15]:
np.set_printoptions(threshold = np.inf)

In [21]:
Alldata=df
non_numerical_columns = Alldata.select_dtypes(exclude=[int, float]).columns.tolist()
Alldata.columns.drop("class")
df2 = pd.DataFrame(Alldata)
df2.to_csv('mydf.txt', sep='\n')

In [22]:
df2.to_csv('mydf.txt', sep='\n')

In [6]:
Alldata[['class']] = Alldata[['class']].replace("B", 0)
Alldata[['class']] = Alldata[['class']].replace("S", 1)



Dropping class column and splitting data


In [7]:
train_split=int(0.8*len(Alldata))
x_train=Alldata[:train_split]
x_test=Alldata[train_split:]
x_test_cpy=x_test
y_train=x_train['class']
y_test=x_test['class']

In [8]:
display(x_train)

transact  bindService  onServiceConnected  ServiceConnection  \
0            0            0                   0                  0   
1            0            0                   0                  0   
2            0            0                   0                  0   
3            0            0                   0                  0   
4            1            1                   1                  1   
...        ...          ...                 ...                ...   
3034         0            0                   0                  0   
3035         0            0                   1                  1   
3036         1            1                   1                  1   
3037         1            1                   1                  1   
3038         1            1                   1                  1   

      android.os.Binder  READ_SMS  attachInterface  WRITE_SMS  \
0                     0         0                0          0   
1                     0         1                0          0   
2                     0         0                0          0   
3                     0         1                0          1   
4                     1         1                1          1   
...                 ...       ...              ...        ...   
3034                  0         0                0          0   
3035                  0         0                0          0   
3036                  1         1                1          1   
3037                  1         0                1          0   
3038                  1         0                1          0   

      TelephonyManager.getSubscriberId  Ljava.lang.Class.getCanonicalName  \
0                                    0                                  0   
1                                    1                                  0   
2                                    0                                  0   
3                                    1                                  0   
4                                    1                                  1   
...                                ...                                ...   
3034                                 0                                  0   
3035                                 0                                  0   
3036                                 0                                  1   
3037                                 0                                  1   
3038                                 0                                  1   

      ...  Ljava.lang.Object.getClass  SET_ORIENTATION  DEVICE_POWER  \
0     ...                           1                0             0   
1     ...                           1                0             0   
2     ...                           0                0             0   
3     ...                           1                0             0   
4     ...                           1                0             1   
...   ...                         ...              ...           ...   
3034  ...                           0                0             0   
3035  ...                           0                0             0   
3036  ...                           1                0             0   
3037  ...                           1                0             0   
3038  ...                           1                0             0   

      EXPAND_STATUS_BAR  GET_TASKS  GLOBAL_SEARCH  GET_PACKAGE_SIZE  \
0                     0          0              0                 0   
1                     0          0              0                 0   
2                     0          0              0                 0   
3                     0          0              0                 0   
4                     0          0              0                 0   
...                 ...        ...            ...               ...   
3034                  0          0              0                 0   
3035                  0   

In [8]:
x_train=x_train.drop(columns='class')
x_test=x_test.drop(columns='class')

In [7]:
display(Alldata[Alldata['class']==1])


transact  bindService  onServiceConnected  ServiceConnection  \
0            0            0                   0                  0   
1            0            0                   0                  0   
2            0            0                   0                  0   
3            0            0                   0                  0   
4            1            1                   1                  1   
...        ...          ...                 ...                ...   
1255         0            0                   0                  0   
1256         0            0                   0                  0   
1257         0            0                   0                  0   
1258         0            0                   0                  0   
1259         0            0                   0                  0   

      android.os.Binder  READ_SMS  attachInterface  WRITE_SMS  \
0                     0         0                0          0   
1                     0         1                0          0   
2                     0         0                0          0   
3                     0         1                0          1   
4                     1         1                1          1   
...                 ...       ...              ...        ...   
1255                  0         1                0          0   
1256                  0         1                0          0   
1257                  0         1                0          1   
1258                  0         0                0          0   
1259                  0         1                0          1   

      TelephonyManager.getSubscriberId  Ljava.lang.Class.getCanonicalName  \
0                                    0                                  0   
1                                    1                                  0   
2                                    0                                  0   
3                                    1                                  0   
4                                    1                                  1   
...                                ...                                ...   
1255                                 1                                  0   
1256                                 0                                  0   
1257                                 1                                  0   
1258                                 1                                  0   
1259                                 0                                  0   

      ...  Ljava.lang.Object.getClass  SET_ORIENTATION  DEVICE_POWER  \
0     ...                           1                0             0   
1     ...                           1                0             0   
2     ...                           0                0             0   
3     ...                           1                0             0   
4     ...                           1                0             1   
...   ...                         ...              ...           ...   
1255  ...                           1                0             0   
1256  ...                           0                0             0   
1257  ...                           1                0             0   
1258  ...                           0                0             0   
1259  ...                           1                0             0   

      EXPAND_STATUS_BAR  GET_TASKS  GLOBAL_SEARCH  GET_PACKAGE_SIZE  \
0                     0          0              0                 0   
1                     0          0              0                 0   
2                     0          0              0                 0   
3                     0          0              0                 0   
4                     0          0              0                 0   
...                 ...        ...            ...               ...   
1255                  0          0              0                 0   
1256                  0   

In [11]:
# Standardize the features
scaler = StandardScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.transform(x_test)

# Convert to PyTorch tensors
X_train_tensor = torch.tensor(x_train, dtype=torch.float32)
y_train_tensor = torch.tensor(y_train.values, dtype=torch.long)
X_test_tensor = torch.tensor(x_test, dtype=torch.float32)
y_test_tensor = torch.tensor(y_test.values, dtype=torch.long)

# Create DataLoader
train_dataset = TensorDataset(X_train_tensor, y_train_tensor)
test_dataset = TensorDataset(X_test_tensor, y_test_tensor)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)


In [12]:
all_predictions = []

In [8]:
import torch.nn as nn
import torch.nn.functional as F

class MalwareDetectionNN(nn.Module):
    def __init__(self, input_size):
        super(MalwareDetectionNN, self).__init__()
        self.fc1 = nn.Linear(input_size, 64)
        self.fc2 = nn.Linear(64, 32)
        self.fc3 = nn.Linear(32, 2)  # 2 output classes: benign or malicious

    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

In [9]:
input_size = x_train.shape[1]
input_size

215

In [15]:
# Initialize model, loss function, and optimizer
input_size = x_train.shape[1]
model = MalwareDetectionNN(input_size)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

# Training loop
epochs = 20
for epoch in range(epochs):
    model.train()
    running_loss = 0.0
    for inputs, labels in train_loader:
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        running_loss += loss.item()

    print(f'Epoch {epoch+1}, Loss: {running_loss/len(train_loader)}')



Epoch 1, Loss: 0.21159221925037472
Epoch 2, Loss: 0.03356178630829642
Epoch 3, Loss: 0.016297425039872332
Epoch 4, Loss: 0.010952544055793337
Epoch 5, Loss: 0.010050275995500239
Epoch 6, Loss: 0.005931126527828287
Epoch 7, Loss: 0.005408157651331031
Epoch 8, Loss: 0.005579780016092915
Epoch 9, Loss: 0.0046300518745594765
Epoch 10, Loss: 0.00448432715091162
Epoch 11, Loss: 0.0032911585425273713
Epoch 12, Loss: 0.0023875338504838416
Epoch 13, Loss: 0.0010903917669901075
Epoch 14, Loss: 0.0027706492835357878
Epoch 15, Loss: 0.0016036929161217766
Epoch 16, Loss: 0.00031778751694410426
Epoch 17, Loss: 0.0005830926600346605
Epoch 18, Loss: 0.00019057900092919131
Epoch 19, Loss: 0.00013213935974004255
Epoch 20, Loss: 0.00011241496198707816


In [16]:
# Evaluate the model
model.eval()
correct = 0
total = 0
with torch.no_grad():
    for inputs, labels in test_loader:
        outputs = model(inputs)
        _, predicted = torch.max(outputs, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

        all_predictions.append(predicted.cpu())  # Append predictions to the list

print(f'Accuracy: {100 * correct / total}%')

Accuracy: 99.34210526315789%


In [17]:
torch.save(model.state_dict(), 'malware_detection_model.pth')

# Load the model
model = MalwareDetectionNN(input_size)
model.load_state_dict(torch.load('malware_detection_model.pth'))


<All keys matched successfully>

In [18]:
all_predictions = torch.cat(all_predictions)

In [19]:
x_test_cpy["predictions"] = all_predictions.numpy()


/tmp/ipykernel_5637/958587183.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x_test_cpy["predictions"] = all_predictions.numpy()


In [20]:
pd.options.display.max_columns = None
pd.options.display.max_rows = None
display(x_test_cpy[x_test_cpy["class"]==0])

transact  bindService  onServiceConnected  ServiceConnection  \
3039         0            1                   1                  1   
3040         1            1                   1                  1   
3041         1            1                   1                  1   
3042         1            1                   1                  1   
3043         0            1                   1                  1   
3044         1            1                   1                  1   
3045         0            0                   0                  0   
3046         1            1                   1                  1   
3047         1            1                   1                  1   
3048         0            0                   0                  0   
3049         1            1                   1                  1   
3050         0            0                   0                  0   
3051         1            1                   1                  1   
3052         0            0                   0                  0   
3053         1            1                   1                  1   
3054         1            1                   1                  1   
3055         1            0                   0                  0   
3056         0            0                   0                  0   
3057         0            0                   0                  0   
3058         1            1                   1                  1   
3059         1            1                   1                  1   
3060         0            0                   0                  0   
3061         0            0                   0                  0   
3062         1            1                   1                  1   
3063         1            1                   1                  1   
3064         0            0                   0                  0   
3065         1            1                   1                  1   
3066         1            1                   1                  1   
3067         1            1                   1                  1   
3068         1            1                   1                  1   
3069         1            1                   1                  1   
3070         1            1                   1                  1   
3071         0            0                   0                  0   
3072         1            1                   1                  1   
3073         0            0                   0                  0   
3074         0            0                   0                  0   
3075         1            1                   1                  1   
3076         0            0                   0                  0   
3077         1            1                   1                  1   
3078         1            1                   1                  1   
3079         1            1                   1                  1   
3080         0            0                   0                  0   
3081         1            1                   1                  1   
3082         0            0                   0                  0   
3083         1            1                   1                  1   
3084         1            1                   1                  1   
3085         1            1                   1                  1   
3086         1            1                   1                  1   
3087         1            1                   1                  1   
3088         1            1                   1                  1   
3089         1            0                   0                  0   
3090         0            0                   0                  0   
3091         0            0                   0                  0   
3092         1            1                   1                  1   
3093         0            0                   0                  0   
3094         1            1                   1                  1   
3095         1  

In [21]:
from azureml.core import Workspace, Run

# Connect to the current run
#run = Run.get_context()

# Register the model
#model = run.register_model(model_name='malgenome_v1', model_path='outputs/malgenome.pkl')

In [22]:
# Save the model to the outputs directory
import joblib
from azureml.core import Model

os.makedirs('outputs', exist_ok=True)
joblib.dump(model, 'outputs/model.pkl')

# Save the final model state
model_save_path = 'final_modelMalgenome.pth'
torch.save(model.state_dict(), model_save_path)
print(f"Saved final model state to {model_save_path}")


Saved final model state to final_modelMalgenome.pth


In [23]:

# Register the model
#model = run.register_model(model_name='your_model_name', model_path='outputs/model.pkl')
model = Model.register(
    workspace=ws,
    model_path=model_save_path,
    model_name='Malgenome2',
    description='A Malgenome neural network for malware detection'
)
# Complete the run
run.complete()

Registering model Malgenome2


In [24]:

# Load the model
model = MalwareDetectionNN(input_size)
model.load_state_dict(torch.load('final_modelMalgenome.pth'))
#model.eval()

<All keys matched successfully>

In [25]:


# Convert to TorchScript
scripted_model = torch.jit.script(model)

# Save the TorchScript model
scripted_model.save('final_modelNaticus_serialized.pt')


## exporting to oonx file

In [26]:

torch.onnx.export(model, dummy_input, "malgenome.onnx", 
                  input_names=['input'], output_names=['output'])

MalwareDetectionNN(
  (fc1): Linear(in_features=215, out_features=64, bias=True)
  (fc2): Linear(in_features=64, out_features=32, bias=True)
  (fc3): Linear(in_features=32, out_features=2, bias=True)
)

In [11]:
pip install onnx

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.9/15.9 MB 60.2 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 309.3/309.3 kB 23.6 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 3.19.6
    Uninstalling protobuf-3.19.6:
      Successfully uninstalled protobuf-3.19.6
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.11.1 requires protobuf<3.20,>=3.9.2, but you have protobuf 5.27.2 which is incompatible.
tensorboard 2.11.2 requires protobuf<4,>=3.9.2, but you have protobuf 5.27.2 which is incompatible.
mlflow-skinny 2.4.1 requires protobuf<5,>=3.12.0, but you have protobuf 5.27.2 which is incompatible.
googleapis-common-protos 1.59.1 requires protobuf!=3.20.0,!=3.20.1,!=4.21.1,!=4.21.2,!=4.21.3,!=4.21.4,!=4.21.5,<5.0.0.dev0,>=3.19.5, but you have protobuf 5.27.2 which is incompatible.


In [2]:
pip install onnx-tf

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 226.1/226.1 kB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 612.0/612.0 kB 12.0 MB/s eta 0:00:00a 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [3]:
import onnx
from onnx_tf.backend import prepare

ImportError: This version of TensorFlow Probability requires TensorFlow version >= 2.13; Detected an installation of version 2.11.1. Please upgrade TensorFlow to proceed.

In [2]:
pip install tensorflow==2.13


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 524.1/524.1 MB 2.0 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 65.2 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 53.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 440.8/440.8 kB 24.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.6/294.6 kB 27.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 59.3 MB/s eta 0:00:0000:0100:01
  Attempting uninstall: tensorflow-estimator
    Found existing installation: tensorflow-estimator 2.11.0
    Uninstalling tensorflow-estimator-2.11.0:
      Successfully uninstalled tensorflow-estimator-2.11.0
  Attempting uninstall: tensorboard-data-server
    Found existing installation: tensorboard-data-server 0.6.1
    Uninstalling tensorboard-data-server-0.6.1:
      Successfully uninstalled tensorboard-data-server-0.6.1
  Attempting uninstall: protobuf
    Found existing instal

In [3]:
pip install protobuf==3.20.*

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 34.9 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.27.2
    Uninstalling protobuf-5.27.2:
      Successfully uninstalled protobuf-5.27.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.11.1 requires protobuf<3.20,>=3.9.2, but you have protobuf 3.20.3 which is incompatible.
azureml-mlflow 1.51.0 requires azure-storage-blob<=12.13.0,>=12.5.0, but you have azure-storage-blob 12.20.0 which is incompatible.
Note: you may need to restart the kernel to use updated packages.


In [ ]:


# Load the ONNX model
onnx_model = onnx.load("malgenome.onnx")

# Convert the ONNX model to TensorFlow
tf_rep = prepare(onnx_model)
tf_rep.export_graph("malgenome.pb")

In [1]:
pip install onnx-tf

Note: you may need to restart the kernel to use updated packages.


In [3]:
onnx-tf convert -i malgenome.onnx -o /outputs

SyntaxError: invalid syntax (3771124926.py, line 1)

In [1]:
import onnx
import tf2onnx
import tensorflow as tf
import numpy as np

# Load the ONNX model
onnx_model_path = "malgenome.onnx"
onnx_model = onnx.load(onnx_model_path)

# Extract the input shape from the ONNX model
def get_input_shape(onnx_model):
    input_tensor = onnx_model.graph.input[0]
    shape = [dim.dim_value for dim in input_tensor.type.tensor_type.shape.dim]
    return shape

input_shape = get_input_shape(onnx_model)

# Create TensorFlow input signature
input_signature = [tf.TensorSpec(input_shape, tf.float32, name="input")]

# Convert the ONNX model to TensorFlow
tf_rep = tf2onnx.tfonnx.tf_optimize(None, None, onnx_model)
tf_rep = tf2onnx.tfonnx.process_tf_graph(tf_rep)

# Export the TensorFlow model
output_path = "path_to_save_your_model"
tf_rep.export_graph(output_path)

# Save the TensorFlow model
with tf.Graph().as_default() as tf_graph:
    tf.import_graph_def(tf_rep.graph.as_graph_def(), name="")
    with tf.compat.v1.Session(graph=tf_graph) as sess:
        tf.compat.v1.saved_model.simple_save(sess, output_path, inputs={"input": tf_graph.get_tensor_by_name("input:0")}, outputs={"output": tf_graph.get_tensor_by_name("output:0")})


2024-07-06 11:25:55.228358: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-07-06 11:25:57.196552: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-07-06 11:25:57.204797: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-06 11:25:59.969963: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


AssertionError: 

In [2]:
pip install onnx_graphsurgeon

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.4/56.4 kB 5.8 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [1]:
import onnx
from onnx2tf import convert

# Load the ONNX model
onnx_model_path = "malgenome.onnx"
onnx_model = onnx.load(onnx_model_path)

# Convert the ONNX model to TensorFlow
output_path = "malgenomeTensor/"
convert(onnx_model_path, output_path)



Model optimizing started ============================================================
Traceback (most recent call last):
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/onnx2tf/onnx2tf.py", line 614, in convert
    result = subprocess.check_output(
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 411, in check_output
    return run(*popenargs, stdout=PIPE, timeout=timeout, check=True,
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 489, in run
    with Popen(*popenargs, **kwargs) as process:
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 854, in __init__
    self._execute_child(args, executable, preexec_fn, close_fds,
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 1702, in _execute_child
    raise child_exception_type(errno_num, err_msg, err_filename)
FileNotFoundError: [Errno 2] No such file or directory: 'onnxsim'


Automatic generation of each O

AttributeError: 'str' object has no attribute 'opset_import'

In [2]:
pip install sng4onnx

Note: you may need to restart the kernel to use updated packages.


In [3]:
from onnx2tf import convert

# Path to your ONNX model
onnx_model_path = "malgenome.onnx"

# Output path for the converted TensorFlow model
output_path = "path_to_save_your_model"

# Convert the ONNX model to TensorFlow
convert(
    input_onnx_file_path=onnx_model_path,
    output_folder_path=output_path
)



Model optimizing started ============================================================
Traceback (most recent call last):
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/onnx2tf/onnx2tf.py", line 614, in convert
    result = subprocess.check_output(
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 411, in check_output
    return run(*popenargs, stdout=PIPE, timeout=timeout, check=True,
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 489, in run
    with Popen(*popenargs, **kwargs) as process:
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 854, in __init__
    self._execute_child(args, executable, preexec_fn, close_fds,
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/subprocess.py", line 1702, in _execute_child
    raise child_exception_type(errno_num, err_msg, err_filename)
FileNotFoundError: [Errno 2] No such file or directory: 'onnxsim'


Automatic generation of each O